In [1]:
import pandas as pd
import numpy as np
import os
import time
import random
import gensim
import numpy as np
import os
import torch
from gensim.models import KeyedVectors
from matplotlib import pyplot as plt
from matplotlib.pyplot import figure

/home/fatma/.local/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
def get_mean_vector(model, words):
    # remove out-of-vocabulary words
    # words: target list words
    # returns average vector for all words in target list
    import numpy as np
    words = [word for word in words if word in model.index_to_key]
    if len(words) >= 1:
        return np.mean(model[words], axis=0)
    else:
        return []

def mdi(mean, gini, weight):
    exp1 =  np.power(mean,weight) 
    exp2 = np.power((1 - gini),1-weight)
    return exp1 * exp2

def get_similarity_Scores(v1,v2):
    from numpy import dot
    from numpy.linalg import norm
    return dot(v1,v2)/(norm(v1)*norm(v2))

def normalize_data(a):
    normalizded_a = []
    amin, amax = min(a), max(a)
    for i in a:
        normalizded_a.append((i-amin) / (amax-amin))
    return normalizded_a
    
def get_similarity_scores_between_target_words_and_attribute_words(model, attribute_words, target_words):
    
    similarity_scores_summary = {}
    words = []
    mean_sim_socres = []

    target_words = [word for word in target_words if word in model.index_to_key]
    attribute_words = [word for word in attribute_words if word in model.index_to_key]
    
    if len(target_words) >= 1 and len(attribute_words) >=1:
        for i in target_words:
            similarity_scores = []
            words.append(i)
            for j in attribute_words:
                cos_sim = get_similarity_Scores(model[i], model[j])
                similarity_scores.append(cos_sim)
            mean_sim_socres.append(np.mean(normalize_data(similarity_scores)))

    similarity_scores_summary["word"] = words
    similarity_scores_summary["mean_sim_score"] = mean_sim_socres
    return similarity_scores_summary

def get_similarity_scores_between_avergare_target_vector_and_attribute_words(model, att_words, target_vector):
    # remove out-of-vocabulary words
    # att_words: wors in the attribute list
    # target_vector: average vector of all words in target group
    similarity_scores_summary = {}
    words_list = []
    similarity_scores = []
    words = [word for word in att_words if word in model.index_to_key]
    print(len(words))
    if len(words) >= 1:
        for i in words:
            print(i)
            words_list.append(i)
            cos_sim = get_similarity_Scores(model[i], target_vector)
            similarity_scores.append(cos_sim)
    similarity_scores_summary["words"] = words_list
    similarity_scores_summary["cos_sim_scores"] = similarity_scores
    similarity_scores_summary["sim_score"] = normalize_data(similarity_scores)

    return similarity_scores_summary


## Read profane words

In [3]:
data_folder = "../../Data/"
embeddings_folder = data_folder+"/word embeddings/"
results_folder = "Results/ethnicity_similarities/glove_CC_large/"

In [4]:
profane_words = open(data_folder+"swear_words.txt").read().splitlines()

## read word embeddings

In [8]:
def get_google_news_embeddings(filename,binary=False):
    w2v_model = gensim.models.KeyedVectors.load_word2vec_format(filename, binary=binary, no_header=True)
    return w2v_model


## word similarity

In [9]:
glove_wk_model = get_google_news_embeddings(embeddings_folder+"/Glove/glove.840B.300d.txt")

## similar words

In [10]:
glove_wk_model.most_similar("girl")

/home/fatma/.local/lib/python3.8/site-packages/gensim/models/keyedvectors.py:772: RuntimeWarning: invalid value encountered in true_divide
  dists = dot(self.vectors[clip_start:clip_end], mean) / self.norms[clip_start:clip_end]


[('girls', 0.8245455622673035),
 ('boy', 0.8148322701454163),
 ('woman', 0.770079493522644),
 ('lady', 0.7557978630065918),
 ('teen', 0.7407616376876831),
 ('sexy', 0.724624514579773),
 ('blonde', 0.695935845375061),
 ('teenage', 0.6914814114570618),
 ('chick', 0.6885995864868164),
 ('babe', 0.688468873500824)]

In [11]:
glove_wk_model.most_similar("queer")

[('queers', 0.6814871430397034),
 ('feminist', 0.6586005687713623),
 ('Queer', 0.6489537358283997),
 ('transgender', 0.6415752172470093),
 ('lgbt', 0.6347734928131104),
 ('transgendered', 0.6329050064086914),
 ('gay', 0.6321444511413574),
 ('homosexual', 0.6258123517036438),
 ('sexuality', 0.5952657461166382),
 ('LGBTQ', 0.593976616859436)]

In [12]:
glove_wk_model.most_similar("queers")

[('homos', 0.7980312705039978),
 ('fags', 0.7023978233337402),
 ('homosexuals', 0.6989225149154663),
 ('faggots', 0.6821241974830627),
 ('queer', 0.6814871430397034),
 ('gays', 0.6647652387619019),
 ('homophobes', 0.6565747261047363),
 ('heteros', 0.6227632164955139),
 ('feminists', 0.6222437024116516),
 ('niggers', 0.6144026517868042)]

In [13]:
glove_wk_model.most_similar("immigrant")

[('immigrants', 0.8647392392158508),
 ('migrant', 0.7003172039985657),
 ('immigration', 0.6988723874092102),
 ('undocumented', 0.6564209461212158),
 ('migrants', 0.6395511031150818),
 ('Immigrant', 0.6290543675422668),
 ('refugee', 0.6281746625900269),
 ('citizenship', 0.604915976524353),
 ('deportation', 0.6023252606391907),
 ('foreign-born', 0.6021814942359924)]

## minority and 
majority words

In [14]:
harmless_majority_words_clean = ["hetrosexual", "cisgender", "man","male","boy","son","father","husband","brother","white","caucasian",
                                 "european american","european", "norwegian", "canadian", "german", "australian", "english",
                                "french", "american", "swedish", "dutch"]

target_words = ["lesbian","gay","bisexual","transgender","tran","queer",
                "lgbt","lgbtq","homosexual", "woman", "female", "girl","wife","sister","daughter","mother", "non-binary",
               "african", "african american", "asian", "black", "hispanic", "latin", "mexican", "indian", "middle eastern",
                "arab"]

words = harmless_majority_words_clean + target_words

In [15]:
profane_vector = get_mean_vector(glove_wk_model, profane_words)
vec_majority_sim_dict = get_similarity_scores_between_avergare_target_vector_and_attribute_words(glove_wk_model, words, profane_vector)
pd.DataFrame(vec_majority_sim_dict).to_csv(results_folder+"_minority_and_majority_words_sim_to_profane_vector.csv")

46
hetrosexual
cisgender
man
male
boy
son
father
husband
brother
white
caucasian
european
norwegian
canadian
german
australian
english
french
american
swedish
dutch
lesbian
gay
bisexual
transgender
tran
queer
lgbt
lgbtq
homosexual
woman
female
girl
wife
sister
daughter
mother
non-binary
african
asian
black
hispanic
latin
mexican
indian
arab


In [16]:
figure(figsize=(25, 10), dpi=1200)
sorted_index = np.argsort(vec_majority_sim_dict["sim_score"])

x_axis = np.arange(len(vec_majority_sim_dict["words"]))
y_axis = [vec_majority_sim_dict["sim_score"][i] for i in sorted_index]
x_ticks = [vec_majority_sim_dict["words"][i] for i in sorted_index]
plt.bar(x_axis, y_axis)
plt.xticks(x_axis, x_ticks, fontsize=40, fontweight='bold', rotation=90)
plt.ylabel("similarity score", fontsize=40, fontweight='bold')
plt.yticks(np.arange(0.1,1.1,0.1),fontsize=40, fontweight='bold')
plt.savefig(results_folder+"similarity_score_of_minority_and_majority_words_to_profanity_vector.pdf", bbox_inches='tight')